In [1]:
import logging
import warnings

# Suppress all warnings
warnings.filterwarnings('ignore')

# Configure root logger
logging.basicConfig(level=logging.ERROR)

# Suppress specific logger warnings from natten.functional
logger = logging.getLogger('natten.functional')
logger.setLevel(logging.ERROR)

# Check if any handlers are attached to the logger, and if not, add one
if not logger.hasHandlers():
    handler = logging.StreamHandler()
    handler.setLevel(logging.ERROR)
    logger.addHandler(handler)



import shutup
shutup.please()

import os
import numpy as np
import random
import math
import json
from functools import partial
from PIL import Image
import pandas as pd

## Imports for plotting
import matplotlib.pyplot as plt
plt.set_cmap('cividis')
%matplotlib inline
from IPython.display import set_matplotlib_formats
set_matplotlib_formats('svg', 'pdf') # For export
from matplotlib.colors import to_rgb
import matplotlib
matplotlib.rcParams['lines.linewidth'] = 2.0
import seaborn as sns
sns.reset_orig()

## tqdm for loading bars
from tqdm.notebook import tqdm

## PyTorch
import torch
import torch.nn as nn
import torch.nn.functional as F
# import torch.utils.npya as data
import torch.optim as optim

## Torchvision
import torchvision
from torchvision import transforms

# PyTorch Lightning
try:
    import pytorch_lightning as pl
except ModuleNotFoundError: # Google Colab does not have PyTorch Lightning installed by default. Hence, we do it here if necessary
    %pip install --quiet pytorch-lightning>=1.4
    import pytorch_lightning as pl
from pytorch_lightning.callbacks import LearningRateMonitor, ModelCheckpoint

# Import tensorboard
%load_ext tensorboard

# Path to the folder where the datasets are/should be downloaded (e.g. CIFAR10)
DATASET_PATH = "../data"
# Path to the folder where the pretrained models are saved
CHECKPOINT_PATH = "../VIT/EMPR"

# # Setting the seed
# pl.seed_everything(64)

# Ensure that all operations are deterministic on GPU (if used) for reproducibility
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

device = torch.device("cuda:0") if torch.cuda.is_available() else torch.device("cpu")
print("Device:", device)


pathstr = r"/media/carol/Data/Documents/Emo_rec/NewMel/Pretraining/Arousal"
model_path = os.path.join(pathstr, "model")
processor_path = os.path.join(pathstr, "processor")
new_model_path = r"/media/carol/Data/Documents/Emo_rec/NewMel/Pretraining/Valence"
model_type = 'DINAT'


# model_path = 'google/vit-base-patch16-224-in21k'
# processor_path = 'google/vit-base-patch16-224-in21k'

Device: cuda:0


<Figure size 640x480 with 0 Axes>

In [2]:
import sys
import warnings

if not sys.warnoptions:
    warnings.simplefilter("ignore")

In [3]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.utils.data as data
device = torch.device("cuda:0") if torch.cuda.is_available() else torch.device("cpu")
print("Device:", device)

Device: cuda:0


In [4]:
from datasets import load_dataset

# train_d0 = load_dataset('cairocode/EMOV_IEMO_MSP_OMG_MSPP')
# train_d0 = load_dataset("cairocode/MSP_POD_Gender2")\
# train_d0 = load_dataset("cairocode/Speaker_Rec_003")

# test_d0 =  load_dataset('cairocode/OMG')
# train_d0 = load_dataset("cairocode/cairocode/IEMOCAP_FULL")
dataset_train = "cairocode/MSPP_SPLIT_MEL2"
train_d0 = load_dataset(dataset_train)
# train_d0 = train_d0['train']
column = "EmoVal"

In [5]:
train_dataset = train_d0['train']
val_dataset = train_d0['validation']
test_dataset = train_d0['test']

In [6]:
# train_dataset = train_d0['train']
# val_dataset = train_d0['validation']
# test_dataset = train_d0['test']

In [7]:

# from transformers import ViTImageProcessor
from transformers import AutoImageProcessor, ViTForImageClassification, ViTHybridForImageClassification, DinatForImageClassification, ViTImageProcessor, ConvNextV2ForImageClassification

# model = ViTHybridForImageClassification.from_pretrained('google/vit-hybrid-base-bit-384', id2label=numtospeak, label2id=speaktonum,  ignore_mismatched_sizes=True)
# model = ViTForImageClassification.from_pretrained(model_path,num_labels = 1, ignore_mismatched_sizes=True, problem_type = "regression")
model = DinatForImageClassification.from_pretrained(model_path,num_labels = 1, ignore_mismatched_sizes=True, problem_type = "regression")

# model = BeitForImageClassification.from_pretrained("microsoft/beit-base-patch16-224" ,id2label=numtospeak, label2id=speaktonum,  ignore_mismatched_sizes=True)

# processor = AutoImageProcessor.from_pretrained("google/vit-hybrid-base-bit-384")
# processor = ViTImageProcessor.from_pretrained(processor_path)
processor = AutoImageProcessor.from_pretrained(processor_path)


# processor = AutoImageProcessor.from_pretrained("facebook/convnextv2-tiny-1k-224")
# model = ConvNextV2ForImageClassification.from_pretrained("facebook/convnextv2-tiny-1k-224")

# model = ViTForImageClassification.from_pretrained("google/vit-base-patch16-224", attn_implementation="sdpa", torch_dtype=torch.float16)
# processor = AutoImageProcessor.from_pretrained("microsoft/beit-base-patch16-224")
# model = BeitForImageClassification.from_pretrained("microsoft/beit-base-patch16-224",id2label=numtospeak, label2id=speaktonum,  ignore_mismatched_sizes=True)


In [8]:
import random
from PIL import Image
from torchvision.transforms import (
    CenterCrop,
    Compose,
    Normalize,
    Resize,
    ToTensor
)

new_size = 224
size = 224


# Define the coordinates of the chunk you want to extract (left, upper, right, lower)
left = 112
upper = 0
right = 224
lower = 75
# Define the six predefined windows as (left, upper, right, lower) tuples
# Add the entire image as an additional option
windows = [
    (0, 0, 112, 75),       # Top-left
    (112, 0, 224, 75),     # Top-right

    (0, 75, 112, 147),     # mid left
    (112, 75, 224, 147),     # Middle-right


    (0, 149, 112, 224),   # bot left
    (112, 149, 224, 224),   # bot right
    None , 
    None, 
    None                   # Entire image
]

class RandomWindowCrop:
    def __init__(self, windows, output_size):
        self.windows = windows
        self.output_size = output_size

    def __call__(self, img):
        window = random.choice(self.windows)
        if window is not None:
            cropped_img = img.crop(window)
        else:
            cropped_img = img
        return cropped_img.resize((self.output_size, self.output_size), Image.BILINEAR)

# Create the new train and validation transform pipelines
_train_transforms = Compose(
    [
        # Resize((new_size, new_size)),
        RandomWindowCrop(windows, size),
        Resize((new_size, new_size)),
        ToTensor(),
        # normalize,
    ]
)

_val_transforms = Compose(
    [
        # Resize((new_size, new_size)),
        # RandomWindowCrop(windows, size),
        Resize((new_size, new_size)),
        ToTensor(),
        # normalize,
    ]
)

def train_transforms(examples):
    examples['pixel_values'] = [_train_transforms(image.convert("RGB")) for image in examples['image']]
    return examples

def val_transforms(examples):
    examples['pixel_values'] = [_val_transforms(image.convert("RGB")) for image in examples['image']]
    return examples



size = 224
windows = [
    None, 
]
_test_transforms = Compose(
    [
        # Resize((new_size, new_size)),
        # RandomWindowCrop(windows, size),
        Resize((new_size, new_size)),
        ToTensor(),
        # normalize,
    ]
)


def test_transforms(examples):
    examples['pixel_values'] = [_test_transforms(image.convert("RGB")) for image in examples['image']]
    return examples




test_dataset.set_transform(test_transforms)

In [9]:
# Set the transforms

train_dataset.set_transform(train_transforms)
val_dataset.set_transform(val_transforms)
# test_dataset.set_transform(val_transforms)

In [10]:
from torch.utils.data import DataLoader
import torch

def collate_fn(examples):
    pixel_values = torch.stack([example["pixel_values"] for example in examples])
    labels = torch.tensor([example[column] for example in examples])
    return {"pixel_values": pixel_values, "labels": labels}

train_batch_size = 30
eval_batch_size = 10

train_dataloader = DataLoader(train_dataset, shuffle=True, collate_fn=collate_fn, batch_size=train_batch_size)
# val_dataloader = DataLoader(val_dataset, collate_fn=collate_fn, batch_size=eval_batch_size)


In [11]:
batch = next(iter(train_dataloader))
for k,v in batch.items():
  if isinstance(v, torch.Tensor):
    print(k, v.shape)

pixel_values torch.Size([30, 3, 224, 224])
labels torch.Size([30])


In [12]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.to(device)


DinatForImageClassification(
  (dinat): DinatModel(
    (embeddings): DinatEmbeddings(
      (patch_embeddings): DinatPatchEmbeddings(
        (projection): Sequential(
          (0): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
          (1): Conv2d(32, 64, kernel_size=(3, 3), stride=(2, 2), padding=(1, 1))
        )
      )
      (norm): LayerNorm((64,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.0, inplace=False)
    )
    (encoder): DinatEncoder(
      (levels): ModuleList(
        (0): DinatStage(
          (layers): ModuleList(
            (0): DinatLayer(
              (layernorm_before): LayerNorm((64,), eps=1e-05, elementwise_affine=True)
              (attention): NeighborhoodAttentionModule(
                (self): NeighborhoodAttention(
                  (query): Linear(in_features=64, out_features=64, bias=True)
                  (key): Linear(in_features=64, out_features=64, bias=True)
                  (value): Linear(in_features

In [13]:

from transformers import TrainingArguments, Trainer

metric_name = "ccc"
# metric_name = "mse"



args = TrainingArguments(
    f"./Gender_logs",
    save_strategy="epoch",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=25,
    per_device_eval_batch_size=25,
    num_train_epochs=20,
    weight_decay=0.03,
    load_best_model_at_end=True,
    metric_for_best_model=metric_name,
    logging_dir='logs',
    remove_unused_columns=False,
)
    

In [14]:
from sklearn.metrics import accuracy_score, recall_score, f1_score, top_k_accuracy_score, mean_squared_error

# def compute_metrics(eval_pred):
#     predictions, labels = eval_pred
#     predicted_classes = (predictions[:, 1] > 0.5).astype(int)
#     accuracy= accuracy_score(labels, predicted_classes)
#     uar = recall_score(labels, predicted_classes, average='macro')
#     f1 = f1_score(labels, predicted_classes, average='macro')
#     return {
#         'accuracy': accuracy, 
#         'uar': uar, 
#         'f1': f1,
#         }


# def compute_metrics(eval_pred):
#     predictions, labels = eval_pred
#     return {"mse": mean_squared_error(labels, predictions)}

# NON BINARY

# from sklearn.metrics import accuracy_score, recall_score, f1_score, top_k_accuracy_score
import numpy as np
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

def concordance_correlation_coefficient(y_true, y_pred):
    mean_true = np.mean(y_true)
    mean_pred = np.mean(y_pred)
    var_true = np.var(y_true)
    var_pred = np.var(y_pred)
    covar = np.cov(y_true, y_pred, rowvar=False)[0, 1]  # Ensure covariance is calculated properly

    numerator = 2 * covar
    denominator = var_true + var_pred + (mean_true - mean_pred) ** 2

    return numerator / denominator


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    # print(eval_pred)
    # print(predictions)
    # print(labels)
    
    mse = mean_squared_error(labels, predictions)
    mae = mean_absolute_error(labels, predictions)
    r2 = r2_score(labels, predictions)
    ccc = concordance_correlation_coefficient(labels, predictions)
    
    return {"mse": mse, 
            "mae": mae, 
            "r2": r2,
            "ccc": ccc}

In [15]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import numpy as np
from scipy.special import lambertw
from transformers import Trainer, TrainingArguments, EarlyStoppingCallback

# Import or define other necessary components (like your model, datasets, etc.)
from typing import Dict  # Add this import
import logging


# class SuperLossRegression(nn.Module):
#     def __init__(self, beta=1.0, lam=1, batch_size=128):
#         super(SuperLossRegression, self).__init__()
#         self.beta = beta  # Scaling parameter, can be related to the standard deviation of the targets
#         self.lam = lam    # Lambda regularization term
#         self.batch_size = batch_size
#         self.tau = math.log(beta)  # Adjust tau based on the scaling parameter

#     def forward(self, predictions, targets):
#         # Adjust predictions and targets to ensure they have the same shape
#         if predictions.dim() == 2 and predictions.size(1) == 1:
#             predictions = predictions.squeeze(-1)  # Convert shape from [batch_size, 1] to [batch_size]

#         if targets.dim() == 2 and targets.size(1) == 1:
#             targets = targets.squeeze(-1)  # Convert shape from [batch_size, 1] to [batch_size]

#         # Compute element-wise MSE loss
#         l_i = F.mse_loss(predictions, targets, reduction='none').detach()
        
#         # Compute sigma using the modified approach for regression
#         sigma = self.sigma(l_i)
        
#         # Compute the modified loss function
#         loss = (F.mse_loss(predictions, targets, reduction='none') - self.tau) * sigma + self.lam * (torch.log(sigma)**2)
        
#         # Normalize the loss by the batch size
#         loss = loss.sum() / self.batch_size
#         return loss

#     def sigma(self, l_i):
#         # Compute sigma for the regression context
#         x = torch.ones(l_i.size()) * (-2 / math.exp(1.))
#         x = x.to(l_i.device)  # Match device (CPU/GPU)
        
#         # Adjust the calculation of y to include tau based on the new scaling parameter
#         y = 0.5 * torch.max(x, (l_i - self.tau) / self.lam)
        
#         # Calculate sigma using the Lambert W function
#         y = y.cpu().numpy()
#         sigma = np.exp(-lambertw(y))
#         sigma = sigma.real.astype(np.float32)
#         sigma = torch.from_numpy(sigma).to(l_i.device)  # Match device (CPU/GPU)
#         return sigma

class SuperTrainer(Trainer):
    def __init__(self, *args, super_loss_params=None, **kwargs):
        super().__init__(*args, **kwargs)
        # Initialize SuperLoss with provided parameters or default values
        if super_loss_params is None:
            super_loss_params = {'lam': 1, 'batch_size': self.args.train_batch_size}

        # self.super_loss = SuperLossRegression(**super_loss_params)
        logging.getLogger().addHandler(logging.NullHandler())
    
        # Disable the natten.functional logger
        logging.getLogger("natten.functional").setLevel(logging.ERROR)

    # def compute_loss(self, model, inputs, return_outputs=False):
    #     """
    #     How the loss is computed by Trainer. By default, all models return the loss in the first element.
    #     """
    #     # Get logits and labels from inputs
    #     outputs = model(**inputs)
    #     logits = outputs.get('logits')
    #     labels = inputs.get('labels')

    #     # Compute the loss using SuperLoss
    #     loss = self.super_loss(logits, labels)
        
    #     return (loss, outputs) if return_outputs else loss
    def log(self, logs: Dict[str, float]) -> None:
        """
        Override the log method to filter out unwanted messages
        """
        filtered_logs = {k: v for k, v in logs.items() if "natten.functional" not in str(k)}
        super().log(filtered_logs)

# Assume `args`, `model`, `train_dataset`, `test_dataset`, `collate_fn`, `compute_metrics`, and `processor` are defined elsewhere in your code

early_stopping = EarlyStoppingCallback(early_stopping_patience=5, early_stopping_threshold=0.001)

super_loss_params = {
    'lam': 1,  # Example value, adjust based on your needs
    'batch_size': args.train_batch_size  # Pass the batch size dynamically
}
# wt_dc = 0.095
trainer = SuperTrainer(
    model=model,
    args=args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    data_collator=collate_fn,
    compute_metrics=compute_metrics,
    tokenizer=processor,
    callbacks=[early_stopping],
    super_loss_params=super_loss_params  # Pass the custom loss parameters here
)


In [16]:
import os
import sys
from contextlib import contextmanager

@contextmanager
def suppress_stdout_stderr():
    with open(os.devnull, "w") as devnull:
        old_stdout = sys.stdout
        old_stderr = sys.stderr
        sys.stdout = devnull
        sys.stderr = devnull
        try:  
            yield
        finally:
            sys.stdout = old_stdout
            sys.stderr = old_stderr

# Use it like this:



In [17]:
import sys
import re
from io import StringIO

class WarningFilter(StringIO):
    def __init__(self, original_stdout):
        super().__init__()
        self.original_stdout = original_stdout

    def write(self, text):
        if not any(warning in text for warning in ['natten.functional', 'deprecated']):
            self.original_stdout.write(text)
        
    def flush(self):
        self.original_stdout.flush()

# Redirect stdout
original_stdout = sys.stdout
sys.stdout = WarningFilter(original_stdout)

try:
    trainer.train()
finally:
    # Restore stdout
    sys.stdout = original_stdout

{'loss': 0.9533, 'grad_norm': 13.893507957458496, 'learning_rate': 1.9837820304897827e-05, 'epoch': 0.16}


{'loss': 0.9059, 'grad_norm': 7.935139179229736, 'learning_rate': 1.9675640609795656e-05, 'epoch': 0.32}


{'loss': 0.8743, 'grad_norm': 23.81666374206543, 'learning_rate': 1.9513460914693484e-05, 'epoch': 0.49}


{'loss': 0.8713, 'grad_norm': 15.911399841308594, 'learning_rate': 1.935128121959131e-05, 'epoch': 0.65}


{'loss': 0.8941, 'grad_norm': 4.99983024597168, 'learning_rate': 1.9189101524489135e-05, 'epoch': 0.81}


...

100%|█████████▉| 839/841 [01:40<00:00,  8.41it/s]
                                                         


{'eval_loss': 0.7741891741752625, 'eval_mse': 0.7741891741752625, 'eval_mae': 0.7032805681228638, 'eval_r2': 0.07234011160233511, 'eval_ccc': 0.23302718028458275, 'eval_runtime': 101.2845, 'eval_samples_per_second': 207.534, 'eval_steps_per_second': 8.303, 'epoch': 12.0}


100%|██████████| 841/841 [01:41<00:00,  8.54it/s]


{'train_runtime': 13930.2239, 'train_samples_per_second': 110.634, 'train_steps_per_second': 4.426, 'train_loss': 0.8035973338439459, 'epoch': 12.0}


 60%|██████    | 36996/61660 [3:52:10<2:34:46,  2.66it/s]


In [18]:
# torch.save(model.state_dict(), '/home/carol/Documents/Emo_rec/MODELS/new_feat_002.pth')

trainer.save_model(os.path.join(new_model_path, "model"))
processor.save_pretrained(os.path.join(new_model_path, "processor"))


# Save the fine-tuned model's state dictionary
# torch.save(model.state_dict(), "D:/Documents/MASC/vIT/ViT/Speaker_pretrain_v2/fine_tuned_model_state_dict.pth")

# Save the tokenizer


['/media/carol/Data/Documents/Emo_rec/NewMel/Pretraining/Valence/processor/preprocessor_config.json']

In [19]:

size = 224
windows = [
    None, 
]
_test_transforms = Compose(
    [
        # Resize((new_size, new_size)),
        RandomWindowCrop(windows, size),
        Resize((new_size, new_size)),
        ToTensor(),
        # normalize,
    ]
)


def test_transforms(examples):
    examples['pixel_values'] = [_test_transforms(image.convert("RGB")) for image in examples['image']]
    return examples




test_dataset.set_transform(test_transforms)
outputs = trainer.predict(test_dataset)
print(outputs.metrics)

100%|██████████| 841/841 [01:40<00:00,  8.38it/s]


{'test_loss': 0.7697354555130005, 'test_mse': 0.7697354555130005, 'test_mae': 0.6971436142921448, 'test_r2': 0.07767673635731709, 'test_ccc': 0.2741025011636276, 'test_runtime': 100.5113, 'test_samples_per_second': 209.131, 'test_steps_per_second': 8.367}


In [20]:
def concordance_correlation_coefficient(y_true, y_pred):
    mean_true = np.mean(y_true)
    mean_pred = np.mean(y_pred)
    var_true = np.var(y_true)
    var_pred = np.var(y_pred)
    covar = np.cov(y_true, y_pred, rowvar=False)[0, 1]  # Ensure covariance is calculated properly

    numerator = 2 * covar
    denominator = var_true + var_pred + (mean_true - mean_pred) ** 2

    return numerator / denominator

def compute_metrics(predictions, labels):

    mse = mean_squared_error(labels, predictions)
    mae = mean_absolute_error(labels, predictions)
    r2 = r2_score(labels, predictions)
    ccc = concordance_correlation_coefficient(labels, predictions)

    print("mse", mse, '\n', 
            "mae",mae, '\n'
            "r2",r2,'\n'
            "ccc", ccc)

In [21]:
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import statsmodels.api as sm
full_path = os.path.join(new_model_path, 'results')
# Sample data
y_true = outputs.label_ids
y_pred = outputs.predictions

y_pred = np.ravel(y_pred)
y_true = np.ravel(y_true)
# Scatter Plot with Regression Line
plt.figure(figsize=(16, 5))

plt.subplot(1, 3, 1)
sns.regplot(x=y_true, y=y_pred, scatter_kws={'alpha':0.5}, line_kws={'color': 'orange'})
plt.title('Scatter Plot with Regression Line')
plt.xlabel('True Labels')
plt.ylabel('Predictions')

# Residual Plot
plt.subplot(1, 3, 2)
residuals = y_pred - y_true
sns.residplot(x=y_true, y=residuals, lowess=False, scatter_kws={'alpha':0.5}, color='purple')
plt.title('Residual Plot')
plt.xlabel('True Labels')
plt.ylabel('Residuals')

# Density Plot
plt.subplot(1, 3, 3)
data = {'True Labels': y_true, 'Predictions': y_pred}
sns.kdeplot(data=data, shade=True, cbar=True)
plt.title('Density Plot')
plt.xlabel('Values')
plt.ylabel('Density')

plt.tight_layout()
plt.show()

plt.savefig(full_path, dpi=300, bbox_inches='tight')
# plt.close(fig)  # Close the figure to free up memory
filename = f"{os.path.split(dataset_train)[1]}ccc{outputs.metrics['test_ccc']:.2f}.png"
save_path = os.path.join(new_model_path, 'results')
os.makedirs(save_path, exist_ok=True)
full_path = os.path.join(save_path, filename)
print(f"Metrics Saved to: {full_path}")

Metrics Saved to: /media/carol/Data/Documents/Emo_rec/NewMel/Pretraining/Valence/results/MSPP_SPLIT_MEL2ccc0.27.png


<Figure size 640x480 with 0 Axes>

In [22]:
compute_metrics(y_pred, y_true)

mse 0.76973546 
 mae 0.6971436 
r2 0.07767673635731709 
ccc 0.2741025011636276


In [23]:
import os
from datetime import datetime


# Ensure the directory exists, create if not
os.makedirs(new_model_path, exist_ok=True)
# Define the file path
file_path = os.path.join(new_model_path, 'header.txt')

# Get the current date
current_date = datetime.now().strftime("%Y-%m-%d")

# Write the content to the file
with open(file_path, 'w') as file:
    file.write(f"Pretrain_file: {pathstr}\n")  # Write the mpath with the label "Pretrain_file:"
    file.write(f"Date: {current_date}\n")   # Write the current date
    file.write(f"Dataset Used: {dataset_train}\n")  
    file.write (f"Model Type: {model_type}\n")
    file.write(f"Column Trained on: {column}\n")
    file.write(f"Test Results: {outputs.metrics}\n")
    # file.write(f"WEIGHT DECAY: {wt_dc}"\n)



print(f"File saved successfully at: {file_path}")

File saved successfully at: /media/carol/Data/Documents/Emo_rec/NewMel/Pretraining/Valence/header.txt
